In [351]:
import plotly.graph_objects as go
import numpy as np
import scipy.constants as cst

## Symétrie :

pour l'études des symétrie il nous faut une distribution homogène (maël avait raison) 

ensuite on se retrouve avec un tuple X,Y,Z il nous suffit de regarder si la distribution est la même en alternant ces termes 

Maillage(X,Y,Z) =? Maillage(Y,Z,X) =? Maillage(Z,X,Y) ...

On pourra en conclure les symétries

In [352]:
def coordonnees_spheriques_to_cartesiennes(r : float, theta : float, phi : float) -> tuple:
    return r*np.sin(theta)*np.cos(phi), r*np.sin(theta)*np.sin(phi), r*np.cos(theta)

def coordonnees_cylindrique_to_cartesiennes(r : float, theta : float, z : float) -> tuple:
    return r*np.cos(theta), r*np.sin(theta), z

def flatten(*vecteurs) : 
    return [vecteur.flatten() for vecteur in vecteurs]

def point(indice, *vecteurs) : 
    return [vecteur[indice] for vecteur in vecteurs]

def charge(X,Y,Z) : 
    """la charge dépend de X Y et Z mais peut etre constante juste pour le calcule on aura charge(point(i,M.XYZ)) ou un truc comme ça"""
    
def distribution() : 
    """je sais pas comment mais faut trouver un moyen pour le calcule formelle davoir sigma"""

In [353]:
class Maillage : 
    def __init__(self,X : np.ndarray ,Y : np.ndarray,Z : np.ndarray) : 
        if X.size == Y.size == Z.size : 
            X,Y,Z = flatten(X,Y,Z)
            self.X = X
            self.Y = Y
            self.Z = Z
            self.XYZ = X,Y,Z
    
    def __add__(self,maillage : "Maillage") -> "Maillage" : 
        X,Y,Z = np.concatenate((self.X,maillage.X)),np.concatenate((self.Y,maillage.Y)),np.concatenate((self.Z,maillage.Z))
        return Maillage(X,Y,Z)
        
    def add_point(self,point : np.ndarray) -> "Maillage" : 
        if point.shape == (3,) : 
            X = self.X + point[0]
            Y = self.Y + point[1]
            Z = self.Z + point[2]

            return Maillage(X,Y,Z)
        
        raise ValueError("Un point est nécéssairement de dimension (3,)")

    
    def __eq__(self, maillage : "Maillage"):
        return np.array_equal(self.X, maillage.X) and \
               np.array_equal(self.Y, maillage.Y) and \
               np.array_equal(self.Z, maillage.Z)
    
    def norme(self) -> np.ndarray : 
        return np.sqrt(self.X**2 + self.Y**2 + self.Z**2)

In [354]:
M1 = Maillage(np.array([1,2,3]),np.array([1,2,3]),np.array([1,2,3]))
M2 = Maillage(np.array([1,2,2]),np.array([1,2,3]),np.array([1,2,3]))

M1 != M2

True

In [355]:
def creer_maillage_cylindrique_3D(z_min : float, z_max : float, rayon : "function", theta : float, n : float):
    #theta = theta - theta%(2*np.pi)
    
    Theta = np.linspace(0,theta, n) 
    Hauteur = np.linspace(z_min,z_max,n)

    THETA, HAUTEUR = np.meshgrid(Theta,Hauteur)
    RAYON = (rayon(Theta,Hauteur) * np.ones((n,n))).T

    return coordonnees_cylindrique_to_cartesiennes(RAYON,THETA,HAUTEUR)

In [356]:
def creer_maillage_spherique_3D(rayon : float, theta : float, phi : float, n : float):
    Theta = np.linspace(0,theta,n) 
    Phi = np.linspace(0,phi,n)

    THETA, PHI = np.meshgrid(Theta,Phi)
    RAYON = (rayon(Theta,Phi) * np.ones((n,n))).T
    
    return coordonnees_spheriques_to_cartesiennes(RAYON,THETA,PHI)

In [357]:
def creer_maillage_disque(rayon, theta,z,n) : 
    Theta = np.linspace(0,theta, n) 
    Rayon = np.linspace(0,rayon, n)
    
    Rayon, Theta = np.meshgrid(Rayon,Theta)
    
    Z = z * np.ones_like(Rayon)

    return coordonnees_cylindrique_to_cartesiennes(Rayon,Theta,Z)

In [358]:
n = 150
r = 2
z = 5
X_d,Y_d,Z_d = creer_maillage_disque(r,2*np.pi,z/2,n)
X_d2,Y_d2,Z_d2 = creer_maillage_disque(r,2*np.pi,-z/2,n)
X_c,Y_c,Z_c = creer_maillage_cylindrique_3D(-z/2,z/2,lambda theta,z :r,2*np.pi,n)

x_flat,y_flat,z_flat = (Maillage(X_d,Y_d,Z_d) + Maillage(X_d2,Y_d2,Z_d2)+ Maillage(X_c,Y_c,Z_c)).XYZ

fig = go.Figure(data=[go.Scatter3d(x=x_flat, y=y_flat, z=z_flat, mode='markers',marker=dict(size=1))])
fig.show()

In [359]:
n = 50

r_cylindre = lambda theta, z : 2
r_sphere = lambda theta,phi : 2

X_c,Y_c,Z_c = creer_maillage_cylindrique_3D(-2,2, r_cylindre, 2*np.pi, n)
X_s,Y_s,Z_s = creer_maillage_spherique_3D(r_sphere, np.pi/2, 2*np.pi, n)
X_s2,Y_s2,Z_s2 = creer_maillage_spherique_3D(r_sphere, np.pi/2, 2*np.pi, n)

maillage_sphere = Maillage(X_s,Y_s,Z_s+2)
maillage_sphere2 = Maillage(X_s2,Y_s2,-Z_s2 - 2)
maillage_cylindre = Maillage(X_c,Y_c,Z_c)

x_flat,y_flat,z_flat = (M := (maillage_sphere + maillage_sphere2 + maillage_cylindre)).XYZ

In [360]:
point = np.array([0,0,0])
M = M.add_point(-point)
Q = 12e-8
N = 7500
q = Q/N
k= 1/(4*np.pi*cst.epsilon_0)

vect = np.sum((k*q/(M.norme()**3)).reshape(1,7500)*M.XYZ,axis=1)

fig = go.Figure(data=[go.Scatter3d(x=x_flat, y=y_flat, z=z_flat, mode='markers',marker=dict(size=1))])
fig.add_trace(go.Scatter3d(x=[point[0], -vect[0]+point[0]], y=[point[1], -vect[1]+point[1]], z=[point[2], -vect[2]+point[2]], mode="lines+markers",marker=dict(size=3)))
fig.show()

In [361]:
p =Maillage(*np.array([3,3,3]))
p.X

np.array([3,3,3]).shape == (3,)

True

In [362]:
n = 100

r_cylindre = lambda theta, z : z

X_s,Y_s,Z_s = creer_maillage_spherique_3D(r_sphere, np.pi, np.pi, n)
X_s2,Y_s2,Z_s2 = creer_maillage_spherique_3D(r_sphere, np.pi/2, 2*np.pi, n)
X_s3,Y_s3,Z_s3 = creer_maillage_spherique_3D(r_sphere, np.pi/2, 2*np.pi, n)
X_s4,Y_s4,Z_s4 = creer_maillage_spherique_3D(r_sphere, np.pi/2, 2*np.pi, n)
X_c,Y_c,Z_c = creer_maillage_cylindrique_3D(-2,2, r_cylindre, 2*np.pi, n)

maillage_cylindre = Maillage(X_c,Y_c,Z_c)
maillage_cylindre2 = Maillage(X_c,Z_c,Y_c)
maillage_cylindre3 = Maillage(Z_c,X_c,Y_c)

maillage_sphere = Maillage(X_s,Y_s+2,Z_s)
maillage_sphere2 = Maillage(X_s2,Y_s2,Z_s2+2)
maillage_sphere3 = Maillage(X_s3,Y_s3,Z_s3)
maillage_sphere4 = Maillage(X_s4,Y_s4,Z_s4)

x_flat,y_flat,z_flat = (maillage_cylindre + maillage_cylindre2 + maillage_cylindre3 + maillage_sphere + maillage_sphere2+ maillage_sphere3).XYZ

fig = go.Figure(data=[go.Scatter3d(x=x_flat, y=y_flat, z=z_flat, mode='markers',marker=dict(size=1))])
fig.show()

In [363]:
n = 100

r = lambda theta, phi : 2
X_s,Y_s,Z_s = creer_maillage_spherique_3D(r, np.pi,2*np.pi, n)

maillage_sphere = Maillage(X_s,Y_s,Z_s) 

x_flat,y_flat,z_flat = maillage_sphere.XYZ

fig = go.Figure(data=[go.Scatter3d(x=x_flat, y=y_flat, z=z_flat, mode='markers',marker=dict(size=1))])
fig.show()

In [364]:
Maillage(X_s,Y_s,Z_s) == Maillage(Z_s,Y_s,X_s) 

False